In [1]:
import numpy as np
import pandas as pd
from astropy.time import Time
import h5py
from pycbc.conversions import mchirp_from_mass1_mass2
from pycbc.conversions import chi_eff
import pylab

In [2]:
gwfile = h5py.File('/work/yifan.wang/3ogcPE/datarelease/3-ogc.hdf','r')

In [3]:
np.size(gwfile['name'][:])

3739087

In [4]:
gwobs = np.array([obs.decode("utf-8") for obs in gwfile['trig'][:]])

# Select those interesting triggers

In [5]:
max_mchirp = mchirp_from_mass1_mass2(2,2)
min_mchirp = mchirp_from_mass1_mass2(1,1)
mc = mchirp_from_mass1_mass2(gwfile['mass1'][:], gwfile['mass2'][:])
spin = chi_eff(gwfile['mass1'][:], gwfile['mass2'][:],gwfile['spin1z'][:], gwfile['spin2z'][:])

lmass = (mc > min_mchirp) & (mc < max_mchirp)
lspin = (spin<0.2) & (spin>-0.2)
ltrig = (gwobs == 'HL') | (gwobs == 'HLV') | (gwobs == 'LV') | (gwobs == 'HV')

yr2min = 365*24*60
lifar = (gwfile['ifar'][:] > 1/yr2min * 10)

l = lmass & lspin & ltrig & lifar

In [6]:
l.sum()

11791

In [7]:
np.where(l)[0]

array([     33,      69,      89, ..., 3738006, 3738471, 3738473])

In [8]:
gwidx = np.where(l)[0]

# FRB

In [9]:
frb = pd.read_csv('./../chimefrbcat1.csv')  
frb_t =  Time(frb['mjd_inf'][:],format='mjd').datetime64

tO3_start = Time('2019-04-01T00:00:00')
tO3_end = Time('2019-09-30T23:59:59')
frb = frb[(frb_t <tO3_end) & (frb_t > tO3_start) & (frb['repeater_name'] == '-9999')] #not a repeated FRB

In [10]:
#add a new column called 'gpstime'
frb['gpstime'] = Time(frb['mjd_inf'][:],format='mjd').gps

In [11]:
frb

tns_name previous_name repeater_name      ra  ra_err ra_notes    dec  \
406  FRB20190401A         -9999         -9999  196.80    0.19    -9999  79.91   
407  FRB20190402A         -9999         -9999  178.61    0.23    -9999  47.10   
408  FRB20190403G         -9999         -9999   81.74    0.22    -9999  25.78   
409  FRB20190403A         -9999         -9999  116.33    0.24    -9999  86.36   
410  FRB20190403B         -9999         -9999  135.47    0.18    -9999   1.46   
..            ...           ...           ...     ...     ...      ...    ...   
595  FRB20190701A         -9999         -9999  277.47    0.21    -9999  59.04   
596  FRB20190701B         -9999         -9999  302.93    0.22    -9999  80.18   
597  FRB20190701C         -9999         -9999   96.36    0.23    -9999  81.63   
598  FRB20190701D         -9999         -9999  112.10    0.18    -9999  66.70   
599  FRB20190701E         -9999         -9999  138.57    0.19    -9999  61.71   

     dec_err dec_notes      gl  ...  sp_run  sp_run_err  high_freq low_freq  \
406    0.210     -9999  122.07  ...    -4.1         1.3      800.2    400.2   
407    0.220     -9999  148.44  ...   -16.7         6.3      657.4    400.2   
408    0.250     -9999  180.44  ...   -76.0        13.0      603.2    425.5   
409    0.290     -9999  126.94  ...    -8.9         2.5      800.2    400.2   
410    0.090     -9999  227.76  ...   -11.1         1.9      714.3    400.2   
..       ...       ...     ...  ...     ...         ...        ...      ...   
595    0.220     -9999   88.29  ...     3.3         1.9      800.2    400.2   
596    0.240     -9999  112.88  ...   -11.8         3.1      732.8    400.2   
597    0.270     -9999  132.18  ...  -211.0        41.0      495.5    402.2   
598    0.160     -9999  149.28  ...   -20.9         1.6      651.8    400.2   
599    0.036     -9999  153.27  ...    -5.1         2.2      800.2    400.2   

     peak_freq      chi_sq     dof  flag_frac  excluded_flag       gpstime  
406      479.1  531748.797  529866      0.433              0  1.238143e+09  
407      453.3  586927.640  582762      0.376              0  1.238224e+09  
408      506.6  448191.356  446874      0.282              0  1.238287e+09  
409      513.6  362788.787  360538      0.421              0  1.238294e+09  
410      453.2  881211.496  878553      0.436              0  1.238300e+09  
..         ...         ...     ...        ...            ...           ...  
595      800.2  341779.300  341690      0.451              0  1.246003e+09  
596      471.5  329229.311  330137      0.470              0  1.246010e+09  
597      446.4  285697.192  286362      0.540              0  1.246045e+09  
598      467.6  358566.724  354457      0.431              0  1.246050e+09  
599      410.3  359241.191  356889      0.427              0  1.246056e+09  

[160 rows x 56 columns]

# There are 160 FRB events satisfying our selection

In [90]:
ra_frb = np.array(frb['ra'])/ 180 * np.pi
dec_frb = np.array(frb['dec']) / 180 * np.pi
t_frb = np.array(frb['gpstime'])
name_frb = np.array(frb['tns_name'])

In [29]:
t_gw = gwfile['time'][gwidx]
name_gw = gwfile['name'][gwidx]
mass1_gw = gwfile['mass1'][gwidx]
mass2_gw = gwfile['mass2'][gwidx]
spin1z_gw = gwfile['spin1z'][gwidx]
spin2z_gw = gwfile['spin2z'][gwidx]
ifar_gw = gwfile['ifar'][gwidx]

# Sort the order

In [14]:
sort1 = t_frb.argsort()
sort2 = t_gw.argsort()
t_frb = t_frb[sort1]
t_gw = t_gw[sort2]

# Time window [-10,3600]

In [15]:
left = np.searchsorted(t_frb, t_gw - 10)
right = np.searchsorted(t_frb, t_gw + 3600)

In [16]:
gwfound = np.where((right - left) > 0)[0]

In [17]:
t_gw[gwfound],name_gw[gwfound],mass1_gw[gwfound],mass2_gw[gwfound],spin1z_gw[gwfound],spin2z_gw[gwfound]

(array([1.2382917e+09, 1.2382924e+09, 1.2382990e+09, 1.2383251e+09,
        1.2383256e+09, 1.2383868e+09, 1.2383873e+09, 1.2384136e+09,
        1.2384154e+09, 1.2384161e+09, 1.2384163e+09, 1.2385188e+09,
        1.2388004e+09, 1.2388023e+09, 1.2388429e+09, 1.2389315e+09,
        1.2389343e+09, 1.2389777e+09, 1.2389915e+09, 1.2389937e+09,
        1.2390437e+09, 1.2390441e+09, 1.2390995e+09, 1.2390999e+09,
        1.2392733e+09, 1.2393875e+09, 1.2394258e+09, 1.2395150e+09,
        1.2396717e+09, 1.2397476e+09, 1.2397486e+09, 1.2397522e+09,
        1.2397528e+09, 1.2397554e+09, 1.2397897e+09, 1.2397911e+09,
        1.2399210e+09, 1.2399419e+09, 1.2400612e+09, 1.2402216e+09,
        1.2402478e+09, 1.2402740e+09, 1.2404381e+09, 1.2404594e+09,
        1.2404613e+09, 1.2404620e+09, 1.2405716e+09, 1.2405732e+09,
        1.2405737e+09, 1.2407412e+09, 1.2408027e+09, 1.2408044e+09,
        1.2408046e+09, 1.2408452e+09, 1.2408454e+09, 1.2408462e+09,
        1.2408471e+09, 1.2419593e+09, 1.2419594e

In [18]:
frbfound = left[gwfound]

In [19]:
t_frb[frbfound],ra_frb[frbfound],dec_frb[frbfound]

(array([1.23829425e+09, 1.23829425e+09, 1.23830040e+09, 1.23832732e+09,
        1.23832732e+09, 1.23838805e+09, 1.23838805e+09, 1.23841634e+09,
        1.23841634e+09, 1.23841634e+09, 1.23841634e+09, 1.23852087e+09,
        1.23880377e+09, 1.23880377e+09, 1.23884542e+09, 1.23893400e+09,
        1.23893447e+09, 1.23897825e+09, 1.23899405e+09, 1.23899405e+09,
        1.23904565e+09, 1.23904565e+09, 1.23910167e+09, 1.23910167e+09,
        1.23927499e+09, 1.23939019e+09, 1.23942901e+09, 1.23951612e+09,
        1.23967179e+09, 1.23974872e+09, 1.23974872e+09, 1.23975528e+09,
        1.23975528e+09, 1.23975809e+09, 1.23979205e+09, 1.23979205e+09,
        1.23992447e+09, 1.23994263e+09, 1.24006272e+09, 1.24022449e+09,
        1.24025074e+09, 1.24027730e+09, 1.24044088e+09, 1.24046288e+09,
        1.24046288e+09, 1.24046288e+09, 1.24057507e+09, 1.24057507e+09,
        1.24057507e+09, 1.24074323e+09, 1.24080621e+09, 1.24080621e+09,
        1.24080621e+09, 1.24084778e+09, 1.24084778e+09, 1.240847

# The time delay of potential concident triggers are

In [94]:
frbfound

array([  3,   3,   4,   5,   5,   9,   9,  10,  10,  10,  10,  11,  14,
        14,  16,  18,  19,  20,  21,  21,  22,  22,  24,  24,  27,  29,
        32,  33,  36,  37,  37,  38,  38,  39,  40,  40,  41,  42,  48,
        53,  54,  55,  56,  57,  57,  57,  58,  58,  58,  63,  65,  65,
        65,  67,  67,  67,  67,  68,  68,  71,  72,  72,  72,  73,  74,
        74,  74,  74,  75,  76,  76,  77,  77,  81,  82,  82,  82,  82,
        82,  83,  83,  83,  84,  84,  85,  85,  90,  90,  90,  91,  93,
        93,  94,  94,  94,  95,  95,  95,  97,  99, 100, 102, 103, 103,
       103, 103, 103, 104, 104, 104, 105, 105, 107, 108, 108, 108, 109,
       112, 112, 112, 113, 114, 114, 115, 116, 117, 118, 119, 122, 122,
       122, 123, 124, 125, 125, 126, 127, 127, 129, 129, 130, 132, 133,
       133, 133, 133, 134, 134, 134, 136, 136, 137, 137, 137, 138, 138,
       138, 138, 141, 141, 141, 141, 144, 144, 144, 145, 146, 148, 148,
       149, 149, 150, 151, 152, 155, 157, 157, 158, 159])

In [95]:
name_frb[frbfound]

array(['FRB20190403A', 'FRB20190403A', 'FRB20190403B', 'FRB20190403C',
       'FRB20190403C', 'FRB20190404A', 'FRB20190404A', 'FRB20190404B',
       'FRB20190404B', 'FRB20190404B', 'FRB20190404B', 'FRB20190405A',
       'FRB20190409A', 'FRB20190409A', 'FRB20190409C', 'FRB20190410A',
       'FRB20190410B', 'FRB20190411A', 'FRB20190411B', 'FRB20190411B',
       'FRB20190411C', 'FRB20190411C', 'FRB20190412A', 'FRB20190412A',
       'FRB20190414B', 'FRB20190415B', 'FRB20190416B', 'FRB20190417B',
       'FRB20190419A', 'FRB20190419B', 'FRB20190419B', 'FRB20190420B',
       'FRB20190420B', 'FRB20190420A', 'FRB20190420C', 'FRB20190420C',
       'FRB20190421B', 'FRB20190422B', 'FRB20190423B', 'FRB20190425A',
       'FRB20190425B', 'FRB20190426A', 'FRB20190427A', 'FRB20190428A',
       'FRB20190428A', 'FRB20190428A', 'FRB20190429A', 'FRB20190429A',
       'FRB20190429A', 'FRB20190501B', 'FRB20190502A', 'FRB20190502A',
       'FRB20190502A', 'FRB20190502C', 'FRB20190502C', 'FRB20190502C',
      

In [103]:
ifrb = []
for n in [b'190519_223219',
b'190623_113752',
b'190617_021148',
b'190518_082303',
b'190419_223729']:
    l = np.where(name_gw[gwfound][:]==n)
    print(l)
    ifrb.append(l[0][0])

(array([79]),)
(array([152]),)
(array([132]),)
(array([69]),)
(array([30]),)


In [104]:
ifrb

[79, 152, 132, 69, 30]

In [105]:
for i in ifrb:
    print(name_frb[frbfound][i])

FRB20190519J
FRB20190623B
FRB20190617A
FRB20190518D
FRB20190419B


In [99]:
t_frb[frbfound] - t_gw[gwfound]

array([2542.68083501, 1902.68083501, 1395.76365161, 2202.08860803,
       1690.08860803, 1233.13834906,  721.13834906, 2772.93877339,
        980.93877339,  212.93877339,   84.93877339, 2089.39056659,
       3386.24815059, 1466.24815059, 2540.50759363, 2543.49900484,
        201.78342438,  582.35167933, 2566.24415779,  390.24415779,
       1936.32384658, 1552.32384658, 2147.00209641, 1763.00209641,
       1644.57568932, 2665.31682563, 3213.88352728, 1116.49551654,
        111.90376663, 1139.05713606,  115.05713606, 3089.03538203,
       2449.03538203, 2702.05536032, 2349.58808661,  941.58808661,
       3450.04193878,  742.12649894, 1538.70868778, 2920.61239481,
       2931.51387477, 3247.47825074, 2733.09724569, 3490.3786931 ,
       1570.3786931 ,  930.3786931 , 3423.88282919, 1887.88282919,
       1375.88282919, 1978.97619963, 3520.86448145, 1856.86448145,
       1600.86448145, 2599.62521124, 2343.62521124, 1575.62521124,
        679.62521124, 1571.12520027, 1443.12520027,  138.31842

In [21]:
len(t_frb[frbfound])

179

In [40]:
ifar_gw[gwfound]

array([1.68026221e-04, 2.51778420e-05, 2.19915182e-05, 1.12129885e-04,
       6.98562435e-05, 2.63957008e-05, 1.92728927e-04, 2.86642353e-05,
       2.17163888e-05, 3.34821852e-05, 1.93443557e-05, 3.81321479e-05,
       5.77287392e-05, 2.47073058e-05, 1.87254671e-04, 1.02682185e-04,
       1.24601007e-04, 5.23329982e-05, 4.01575926e-05, 2.66404659e-05,
       1.93393480e-05, 2.35573880e-05, 3.07839036e-05, 8.84523979e-05,
       2.81654084e-05, 3.61142855e-04, 2.06161174e-04, 3.71845235e-05,
       2.68342774e-05, 1.01035075e-04, 4.60939591e-05, 1.20328383e-04,
       1.42984791e-04, 4.70042614e-05, 2.43043556e-04, 5.75477898e-04,
       2.63119407e-04, 1.15590432e-04, 5.43132883e-05, 4.52367058e-05,
       2.62051908e-05, 4.64864352e-05, 3.12808188e-05, 1.45768907e-04,
       2.13304847e-05, 4.10004795e-05, 3.45568260e-05, 2.06291315e-05,
       3.00097399e-05, 2.04051612e-05, 1.02942919e-04, 2.04298718e-04,
       7.84479853e-05, 3.05423891e-05, 2.30559788e-04, 1.96468027e-04,
      

In [64]:
data = np.array(np.column_stack((name_gw[gwfound], ifar_gw[gwfound])),dtype=[('S16',float)])

In [65]:
data

array([[(1.90403016e+11,), (1.68026220e-04,)],
       [(1.90403020e+11,), (2.51778420e-05,)],
       [(1.90403036e+11,), (2.19915180e-05,)],
       [(1.90403111e+11,), (1.12129885e-04,)],
       [(1.90403112e+11,), (6.98562400e-05,)],
       [(1.90404042e+11,), (2.63957000e-05,)],
       [(1.90404043e+11,), (1.92728930e-04,)],
       [(1.90404115e+11,), (2.86642350e-05,)],
       [(1.90404122e+11,), (2.17163890e-05,)],
       [(1.90404123e+11,), (3.34821850e-05,)],
       [(1.90404123e+11,), (1.93443560e-05,)],
       [(1.90405166e+11,), (3.81321480e-05,)],
       [(1.90408231e+11,), (5.77287400e-05,)],
       [(1.90408234e+11,), (2.47073060e-05,)],
       [(1.90409110e+11,), (1.87254670e-04,)],
       [(1.90410114e+11,), (1.02682185e-04,)],
       [(1.90410122e+11,), (1.24601000e-04,)],
       [(1.90411003e+11,), (5.23329980e-05,)],
       [(1.90411042e+11,), (4.01575930e-05,)],
       [(1.90411045e+11,), (2.66404660e-05,)],
       [(1.90411185e+11,), (1.93393480e-05,)],
       [(1.90

In [98]:
import h5py
f = h5py.File('/work/yifan.wang/em/prod1/gw_triggers.hdf', 'w')
f.create_dataset('gwname', data=name_gw[gwfound])
f.create_dataset('gwifar', data=ifar_gw[gwfound])
f.create_dataset('frbname',data=name_frb[frbfound])
f.close()

# 179 triggers detected
# Print the triggers. Two sets: with ra, dec and without ra,dec

In [140]:
noskydir = '/work/yifan.wang/em/prod1/nosky/triggers/'

io3a = 0

for ii in gwfound:
    print('#########################')
    print('Trigger from GRB/GW search: ',name_gw[ii])

    with open(noskydir + 'o3a_trigger_'+str(io3a)+'_nosky.ini', 'w') as t:
        t.write('[trigger]\nmass1=%f\nmass2=%f\nspin1z=%f\nspin2z=%f\ntrigger_time=%f' %   
                (mass1_gw[ii],mass2_gw[ii],
                 spin1z_gw[ii],spin2z_gw[ii],
                 t_gw[ii]))
        t.close()
        io3a  +=1

#########################
Trigger from GRB/GW search:  b'190403_015506'
#########################
Trigger from GRB/GW search:  b'190403_020441'
#########################
Trigger from GRB/GW search:  b'190403_035529'
#########################
Trigger from GRB/GW search:  b'190403_111054'
#########################
Trigger from GRB/GW search:  b'190403_111922'
#########################
Trigger from GRB/GW search:  b'190404_041922'
#########################
Trigger from GRB/GW search:  b'190404_042729'
#########################
Trigger from GRB/GW search:  b'190404_114505'
#########################
Trigger from GRB/GW search:  b'190404_121518'
#########################
Trigger from GRB/GW search:  b'190404_122733'
#########################
Trigger from GRB/GW search:  b'190404_123131'
#########################
Trigger from GRB/GW search:  b'190405_165956'
#########################
Trigger from GRB/GW search:  b'190408_231300'
#########################
Trigger from GRB/GW search:  b'190408_

In [153]:
noskydir = '/work/yifan.wang/em/prod1/nosky/triggers/'
eventdir = '/work/yifan.wang/em/prod1/nosky/events_nosky.ini'
o3a = 0
with open(eventdir, 'w') as t:
    
    for ii in gwfound:
        print('#########################')
        print('Trigger from GRB/GW search: ',name_gw[ii])
        t.write('[event-o3a_'+str(name_gw[ii].decode())+']\nlabel='+str(name_gw[ii].decode())+'\nconfig-files=nosky_inference.ini\n\t\to3a.ini\n\t\ttriggers/o3a_trigger_'+str(o3a)+'_nosky.ini\n\n')
        o3a = o3a+1
t.close()

#########################
Trigger from GRB/GW search:  b'190403_015506'
#########################
Trigger from GRB/GW search:  b'190403_020441'
#########################
Trigger from GRB/GW search:  b'190403_035529'
#########################
Trigger from GRB/GW search:  b'190403_111054'
#########################
Trigger from GRB/GW search:  b'190403_111922'
#########################
Trigger from GRB/GW search:  b'190404_041922'
#########################
Trigger from GRB/GW search:  b'190404_042729'
#########################
Trigger from GRB/GW search:  b'190404_114505'
#########################
Trigger from GRB/GW search:  b'190404_121518'
#########################
Trigger from GRB/GW search:  b'190404_122733'
#########################
Trigger from GRB/GW search:  b'190404_123131'
#########################
Trigger from GRB/GW search:  b'190405_165956'
#########################
Trigger from GRB/GW search:  b'190408_231300'
#########################
Trigger from GRB/GW search:  b'190408_

# Make sky triggers

In [159]:
skydir = '/work/yifan.wang/em/prod1/sky/triggers/'

io3a = 0

for ii,vv in enumerate(gwfound):
    print('#########################')
    print('Trigger from GRB/GW search: ',name_gw[vv])

    with open(skydir + 'o3a_trigger_'+str(io3a)+'_sky.ini', 'w') as t:
        t.write('[trigger]\nmass1=%f\nmass2=%f\nspin1z=%f\nspin2z=%f\nra=%f\ndec=%f\ntrigger_time=%f' %   
                (mass1_gw[vv],mass2_gw[vv],
                 spin1z_gw[vv],spin2z_gw[vv],
                 ra_frb[frbfound][ii],dec_frb[frbfound][ii],
                 t_gw[vv]))
        t.close()
        io3a  +=1

#########################
Trigger from GRB/GW search:  b'190403_015506'
#########################
Trigger from GRB/GW search:  b'190403_020441'
#########################
Trigger from GRB/GW search:  b'190403_035529'
#########################
Trigger from GRB/GW search:  b'190403_111054'
#########################
Trigger from GRB/GW search:  b'190403_111922'
#########################
Trigger from GRB/GW search:  b'190404_041922'
#########################
Trigger from GRB/GW search:  b'190404_042729'
#########################
Trigger from GRB/GW search:  b'190404_114505'
#########################
Trigger from GRB/GW search:  b'190404_121518'
#########################
Trigger from GRB/GW search:  b'190404_122733'
#########################
Trigger from GRB/GW search:  b'190404_123131'
#########################
Trigger from GRB/GW search:  b'190405_165956'
#########################
Trigger from GRB/GW search:  b'190408_231300'
#########################
Trigger from GRB/GW search:  b'190408_

In [161]:
eventdir = '/work/yifan.wang/em/prod1/sky/events_sky.ini'
o3a = 0
with open(eventdir, 'w') as t:
    
    for ii in gwfound:
        print('#########################')
        print('Trigger from GRB/GW search: ',name_gw[ii])
        t.write('[event-o3a_'+str(name_gw[ii].decode())+']\nlabel='+str(name_gw[ii].decode())+'\nconfig-files=sky_inference.ini\n\t\to3a.ini\n\t\ttriggers/o3a_trigger_'+str(o3a)+'_sky.ini\n\n')
        o3a = o3a+1
t.close()

#########################
Trigger from GRB/GW search:  b'190403_015506'
#########################
Trigger from GRB/GW search:  b'190403_020441'
#########################
Trigger from GRB/GW search:  b'190403_035529'
#########################
Trigger from GRB/GW search:  b'190403_111054'
#########################
Trigger from GRB/GW search:  b'190403_111922'
#########################
Trigger from GRB/GW search:  b'190404_041922'
#########################
Trigger from GRB/GW search:  b'190404_042729'
#########################
Trigger from GRB/GW search:  b'190404_114505'
#########################
Trigger from GRB/GW search:  b'190404_121518'
#########################
Trigger from GRB/GW search:  b'190404_122733'
#########################
Trigger from GRB/GW search:  b'190404_123131'
#########################
Trigger from GRB/GW search:  b'190405_165956'
#########################
Trigger from GRB/GW search:  b'190408_231300'
#########################
Trigger from GRB/GW search:  b'190408_